In [15]:
### Basic imports ###
import sys, os
import scipy
from scipy import stats

# For plotting
from chart_studio import plotly
import plotly as pltly
import plotly.graph_objs as go
import plotly.offline as pltlyoff
from IPython.display import display, HTML

# This is for plotting as static images (to show on e.g. GitHub)
import plotly.io as pio
from IPython.display import Image

# Numerics
import numpy as np
import scipy as sp
import itertools
import pyDOE

### Custom files ###
dir_GPPlotly = 'C:\\Users\\tln229\\Downloads\\Python Tests\\Constrained GP_2\\GP_2\\gp_plotly\\'
sys.path.append(dir_GPPlotly)

dir_gp_constr = 'C:\\Users\\tln229\\Downloads\\Python Tests\\Constrained GP_2\\GP_2\\gp_constr\\'
sys.path.append(dir_gp_constr)

# Import
from GPPlotly.plottingfunctions import PlotGP2d, add_traces_to_fig
from GPConstr.model import GPmodel, Constraint
from GPConstr.kern import kernel_RBF

### Setup notebook ###
pltlyoff.init_notebook_mode(connected=True)
print('Python version', sys.version)

Python version 3.10.5 (tags/v3.10.5:f377153, Jun  6 2022, 16:14:13) [MSC v.1929 64 bit (AMD64)]


In [16]:
# Function to emulate/estimate
def fun(x):
    return (np.arctan(20*x - 10) - np.arctan(-10))/3

In [17]:
# Design data - no noise
x_design = np.array([1/(n+2) for n in range(7)] ) + 0.1
y_design = fun(x_design)

# For plotting
x_test = np.linspace(0, 1, 500)
y_true = fun(x_test)

In [18]:
# Set up model
ker = kernel_RBF(variance = 0.5, lengthscale = [0.1])
model = GPmodel(kernel = ker, likelihood = 1E-6, mean = 0) # No Noise

# Add the training data
model.X_training = x_design.reshape(-1, 1)
model.Y_training = y_design

In [19]:
# Plot unconstrained un-optimized GP
mean_unconstr, cov_unconstr = model.calc_posterior_unconstrained(x_test.reshape(-1, 1), full_cov = True)
mean_unconstr = np.array(mean_unconstr).flatten()
var_unconstr = np.diagonal(cov_unconstr)

num_samples = 30
show_samplepaths = True
samplepaths_unconstr = []
if show_samplepaths: samplepaths_unconstr = np.random.multivariate_normal(mean_unconstr, cov_unconstr, num_samples).T

fig_unconstr_1 = PlotGP2d(x_mean = x_test, mean = mean_unconstr, var = var_unconstr,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        num_std = 1.2815,
                        x_true = x_test, y_true = y_true,
                        samplepaths = samplepaths_unconstr,
                        title = 'Unconstrained GP', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

pltlyoff.iplot(fig_unconstr_1, filename='')

..Running calculation of K_w ... DONE - time: 0.000 seconds
..Running calculation of Cholesky factor for K_w ... DONE - time: 0.000 seconds
..Calculating f* | Y ... DONE - Total time: 0.006 seconds


In [20]:
# Helper functions for constraints
def constant_function(val):
    """ Return the constant function"""
    def fun(x):
        return np.array([val]*x.shape[0])
    
    return fun

def fun_UB(x):
    """ Upper bound function """
    return np.log(30*x.flatten() + 1)/3 + 0.1

In [21]:
# Define constraints for bounding the function and its derivative
constr_bounded = Constraint(LB = constant_function(0), UB = fun_UB)
constr_deriv = Constraint(LB = constant_function(0), UB = constant_function(float('Inf')))

In [22]:
# Add only boundedness constraint to model
model.constr_bounded = constr_bounded
model.constr_likelihood = 1E-6

In [23]:
# Search for a suitable set of virtual observation locations where the constraint is imposed
df, num_pts, pc_min = model.find_XV_subop(bounds = [(0.001, 1)], p_target = 0.99, i_range = [0], print_intermediate = True) # (Some intermediate calcs are stored in df)
XV_bound = model.constr_bounded.Xv # (Extract the virtual observation locations for plotting)

# Note: Alternatively we can set these points manually, 
# e.g. model.constr_bounded.Xv = np.linspace(0, 1, 20).reshape(-1, 1)

Searching for points XV s.t. P(a - nu < Lf < b + nu) > p_target = 0.99 for Lf = [f] and nu = 2.326347874040841e-06 ...
i = 0, XV[1] = [0.00100138], prob = 0.06708730543156662, optimization time = 0.054 seconds
i = 0, XV[2] = [0.93976331], prob = 0.4596356501594267, optimization time = 0.028 seconds
i = 0, XV[3] = [0.06879572], prob = 0.5493290435372554, optimization time = 0.049 seconds
i = 0, XV[4] = [0.78470123], prob = 0.578011796220867, optimization time = 0.035 seconds
i = 0, XV[5] = [0.68731626], prob = 0.8261433235092112, optimization time = 0.062 seconds
i = 0, XV[6] = [0.99999926], prob = 0.7482078228110606, optimization time = 0.131 seconds
i = 0, XV[7] = [0.86808928], prob = 0.8462360958825361, optimization time = 0.053 seconds
i = 0, XV[8] = [0.15037412], prob = 0.8845925981588525, optimization time = 0.054 seconds
i = 0, XV[9] = [0.73699805], prob = 0.9512060026539918, optimization time = 0.063 seconds
i = 0, XV[10] = [0.83316859], prob = 0.9769416805424209, optimization t

In [24]:
# Print the model
print(model)

----- GP model ----- 
 mean = 0 
 likelihood = 1e-06 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.1] 
   variance = 0.5 
 constraint: 
   f [15] 
   constr_likelihood = 1e-06 
---------------------


In [25]:
# Plot model with boundedness constraint
mean, var, perc, mode, samples, times = model.calc_posterior_constrained(x_test.reshape(-1, 1), compute_mode = False, num_samples = 10000, save_samples = 30, algorithm = 'minimax_tilting', resample = False)

mean = np.array(mean).flatten()
p_lower = perc[0]
median = perc[1]
p_upper = perc[2]
p_label = '[p{}, p{}]'.format(10, 90)
samplepaths_Z = np.array(samples)
    
# Get GP figure
fig_bounded = PlotGP2d(x_mean = x_test, mean = mean,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        samplepaths =  samplepaths_Z,
                        x_true = x_test, y_true = y_true,
                        p_lower = p_lower, p_upper = p_upper, p_label = p_label,
                        title = 'Boundedness constraint', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

# Add traces for bounds and virtual observation locations
trace_UB = go.Scatter(x = x_test, y = model.constr_bounded.UB(x_test), mode = 'lines', name = 'Upper bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_LB = go.Scatter(x = x_test, y = model.constr_bounded.LB(x_test), mode = 'lines', name = 'Lower bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_XV_bounded = go.Scatter(x = model.constr_bounded.Xv.flatten(), y = np.zeros(model.constr_bounded.Xv.shape[0]), mode = 'markers', name = 'Xv - boundedness', marker = dict(symbol = 'line-ns-open', color = ('rgb(0, 0, 0)')))
fig_bounded = add_traces_to_fig(fig_bounded, [trace_UB, trace_LB, trace_XV_bounded])

pltlyoff.iplot(fig_bounded, filename='')

..Running calculation of K_w ... SKIP - (cached)
..Running calculation of Cholesky factor for K_w ... SKIP - (cached)
..Running preparation step 1 - dependence on (XS, X) ... DONE - time: 0.011 seconds
..Running preparation step 2 - dependence on (XV, X) ... SKIP - (cached)
..Running preparation step 3 - dependence on (XS, XV, X) ... DONE - time: 0.002 seconds
..sampling 10000 times from truncated constraint distribution C~|C, Y DONE - time: 0.089 seconds
..sampling 10000 times from constrained GP f*|C, Y DONE - time: 0.569 seconds
..computing statistics from samples DONE - time: 0.143 seconds
 DONE - Total time: 0.814 seconds


In [26]:
# Reset model (clear cache)
model.reset()

constr_bounded.Xv = None
model.constr_bounded = constr_bounded

constr_deriv.Xv = None
model.constr_deriv = [constr_deriv] # Add list of constraints for multi-dimensional functions

print(model)

----- GP model ----- 
 mean = 0 
 likelihood = 1e-06 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.1] 
   variance = 0.5 
 constraint: 
   f [0], df/dx_1 [0] 
   constr_likelihood = 1e-06 
---------------------


In [27]:
# Search for a suitable set of virtual observation locations where the constraint is imposed
df, num_pts, pc_min = model.find_XV_subop(bounds = [(0.001, 1)], p_target = 0.9, i_range = [0, 1], print_intermediate = True)

Searching for points XV s.t. P(a - nu < Lf < b + nu) > p_target = 0.9 for Lf = [f, df/dx_1] and nu = 1.2815515655446004e-06 ...
i = 0, XV[1] = [0.00100058], prob = 0.06708118851916223, optimization time = 0.077 seconds
i = 1, XV[2] = [0.70576254], prob = 0.16443126900321386, optimization time = 0.082 seconds
i = 1, XV[3] = [0.86452578], prob = 0.10596185001237134, optimization time = 0.143 seconds
i = 1, XV[4] = [1.], prob = 0.1101106783076956, optimization time = 0.149 seconds
i = 1, XV[5] = [0.62176485], prob = 0.3486122365633796, optimization time = 0.179 seconds
i = 1, XV[6] = [0.78379689], prob = 0.1649028759733749, optimization time = 0.152 seconds
i = 0, XV[7] = [0.92121165], prob = 0.12417099187382542, optimization time = 0.126 seconds
i = 1, XV[8] = [0.07394108], prob = 0.38401659259046733, optimization time = 0.110 seconds
i = 1, XV[9] = [0.18366956], prob = 0.3679015611411553, optimization time = 0.138 seconds
i = 1, XV[10] = [0.001], prob = 0.006449178749420423, optimizatio

In [28]:
mean, var, perc, mode, samples, times = model.calc_posterior_constrained(x_test.reshape(-1, 1), compute_mode = False, num_samples = 10000, save_samples = 30, algorithm = 'minimax_tilting', resample = False)

mean = np.array(mean).flatten()
p_lower = perc[0]
median = perc[1]
p_upper = perc[2]
p_label = '[p{}, p{}]'.format(10, 90)

samplepaths_Z = np.array(samples)

fig_both = PlotGP2d(x_mean = x_test, mean = mean,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        p_lower = p_lower, p_upper = p_upper, p_label = p_label,
                        samplepaths =  samplepaths_Z,
                        x_true = x_test, y_true = y_true,
                        title = 'Both constraints', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

trace_XV_bounded = go.Scatter(x = model.constr_bounded.Xv.flatten(), y = np.zeros(model.constr_bounded.Xv.shape[0]), mode = 'markers', name = 'Xv - boundedness', marker = dict(symbol = 'line-ns-open', color = ('rgb(0, 0, 0)')))
trace_XV_mon = go.Scatter(x = model.constr_deriv[0].Xv.flatten(), y = np.zeros(model.constr_deriv[0].Xv.shape[0]), mode = 'markers', name = 'Xv - monotonicity', marker = dict(symbol = 'x-thin-open', color = ('rgb(0, 0, 0)')))

fig_both = add_traces_to_fig(fig_both, [trace_UB, trace_LB, trace_XV_bounded, trace_XV_mon])

pltlyoff.iplot(fig_both, filename='')

..Running calculation of K_w ... SKIP - (cached)
..Running calculation of Cholesky factor for K_w ... SKIP - (cached)
..Running preparation step 1 - dependence on (XS, X) ... DONE - time: 0.012 seconds
..Running preparation step 2 - dependence on (XV, X) ... SKIP - (cached)
..Running preparation step 3 - dependence on (XS, XV, X) ... DONE - time: 0.002 seconds
..sampling 10000 times from truncated constraint distribution C~|C, Y DONE - time: 3.583 seconds
..sampling 10000 times from constrained GP f*|C, Y DONE - time: 0.536 seconds
..computing statistics from samples DONE - time: 0.138 seconds
 DONE - Total time: 4.272 seconds
